# Example use case: Binary black hole systems
TODO: introduce the notebook


In [1]:
import os
from binarycpython.utils.functions import temp_dir
from binarycpython.utils.run_system_wrapper import run_system
TMP_DIR = temp_dir("notebooks", "notebook_BHBH")

In [2]:
log_filename = "log_file"
output = run_system(M_1=60, 
                    BH_prescription='BH_BELCZYNSKI',
                    log_filename=log_filename, 
                    api_log_filename_prefix=TMP_DIR)
with open(log_filename, 'r') as f:
    print(f.read())

      TIME      M1       M2   K1  K2           SEP        PER   ECC  R1/ROL1 R2/ROL2  TYPE RANDOM_SEED=30441 RANDOM_COUNT=0
     0.0000   60.000    0.000  1  15            -1       -1   -1.00   0.000   0.000  "INITIAL "
     6.1193   28.792    0.000  1  15            -1       -1   -1.00   0.000   0.000  "Start Carbon Star 1"
     6.6492   26.756    0.000  2  15            -1       -1   -1.00   0.000   0.000  "OFF_MS"
     6.6492   26.756    0.000  2  15            -1       -1   -1.00   0.000   0.000  "TYPE_CHNGE"
     6.6588   26.687    0.000  4  15            -1       -1   -1.00   0.000   0.000  "TYPE_CHNGE"
     7.2135    9.972    0.000  7  15            -1       -1   -1.00   0.000   0.000  "TYPE_CHNGE"
     7.2135    9.972    0.000  7  15            -1       -1   -1.00   0.000   0.000  "End Carbon Star 1"
     7.3695    9.813    0.000  8  15            -1       -1   -1.00   0.000   0.000  "TYPE_CHNGE"
     7.3967    8.827    0.000 14  15            -1       -1   -1.00   0.000   0.00

Now we start a binary in a very wide orbit, so the stars do not interact (except by a little wind accretion). This makes a "14 14", i.e. BH+BH, pair.

In [3]:
output = run_system(M_1=60, 
                    M_2=40,
                    orbital_period=2000, # days
                    BH_prescription='BH_BELCZYNSKI',
                    log_filename=log_filename, 
                    wind_mass_loss='WIND_ALGORITHM_BINARY_C_2020',
                    api_log_filename_prefix=TMP_DIR)
with open(log_filename, 'r') as f:
    print(f.read())

      TIME      M1       M2   K1  K2           SEP        PER   ECC  R1/ROL1 R2/ROL2  TYPE RANDOM_SEED=35895 RANDOM_COUNT=0
     0.0000   60.000   40.000  1   1        3101.2     5.48 y  0.00   0.009   0.009  "INITIAL "
     0.0000   60.000   40.000  1   1        3101.2     5.48 y  0.00   0.009   0.009  "BEG_SYMB"
     4.3583   42.081   35.930  1   1          3971     8.98 y  0.00   0.023   0.014  "Start tidal lock 1"
     4.3928   41.632   35.894  1   1        3995.8      9.1 y  0.00   0.023   0.014  "End tidal lock 1"
     6.1199   28.792   28.776  1   1        5374.9     16.5 y  0.00   0.014   0.014  "Start Carbon Star 1"
     6.4219   27.615   27.603  1   1        5603.4     17.9 y  0.00   0.013   0.013  "Start tidal lock 2"
     6.5403   27.157   27.151  1   1        5696.9     18.5 y  0.00   0.012   0.012  "End tidal lock 2"
     6.6475   26.763   26.731  2   1        5791.5     19.1 y  0.00   0.010   0.011  "TYPE_CHNGE"
     6.6548   26.730   26.729  2   1        5794.3     19.1

So let's write a function to detect BHBH pairs.

In [4]:

# BHBH detector : returns BHBH system data, or None if not found 
def BHBH(filename):
    vb = False # set to True for debugging
    with open(filename, 'r') as f:
        for line in f.readlines():
            data = line.split()
            if vb == True:
                print ('data line ', line)
                print ('length ' + str(len(data)))
            if len(data) >= 10 and data[0] != 'TIME': 
                stellar_type1 = int(data[3])
                stellar_type2 = int(data[4])
            
                # remember: stellar type 14 == BH
                if stellar_type1 == 14 and stellar_type2 == 14:
                    # BHBH system
                    if vb == True:
                        print ('FOUND BHBH system')
                        print (line)
                    names = ['time','M1','M2','K1','K2','separation']
                    d = {}
                    for name in names:
                        d[name] = float(data.pop(0))
                        if vb == True:
                            print(data)
                    f.close()
                    return d

data = BHBH(log_filename)
if data == None or len(data) == 0:
    print("Oops: no data found")
if data['separation'] < 0.0:
    print("BHBH system is unbound")
else:
    print("BHBH system is bound")

BHBH system is unbound


In [5]:
def search_for_BHBH(maxcount,**opts):
    print(opts)
    found = False
    count = 0
    while found == False and count < maxcount:
        count = count + 1
        print("system {} / {}".format(count,maxcount))
        output = run_system(**opts,
                            log_filename=log_filename, 
                            api_log_filename_prefix=TMP_DIR,
                            )
        data = BHBH(log_filename)
        print (data)
        
        if data == None or len(data) == 0:
            # no BHBH found  
            found = False
        else:
            print("System {count} has separation {sep}".format(count=count,sep=data['separation']))
            if data['separation'] > 0.0:
                # found bound BHBH system
                print('Found bound BHBH system')
                found = True
        
                # show the log file
                with open(log_filename, 'r') as f:
                    print(f.read())

args = dict(
            M_1=60, 
            M_2=40,
            orbital_period=2000, # days
            BH_prescription='BH_FRYER12_RAPID',
            wind_mass_loss='WIND_ALGORITHM_BINARY_C_2020',
           )
search_for_BHBH(100,**args)


{'M_1': 60, 'M_2': 40, 'orbital_period': 2000, 'BH_prescription': 'BH_FRYER12_RAPID', 'wind_mass_loss': 'WIND_ALGORITHM_BINARY_C_2020'}
system 1 / 100
{'time': 7.4046, 'M1': 5.851, 'M2': 5.873, 'K1': 14.0, 'K2': 14.0, 'separation': -510.17}
System 1 has separation -510.17
system 2 / 100
{'time': 7.4046, 'M1': 5.851, 'M2': 5.873, 'K1': 14.0, 'K2': 14.0, 'separation': -60.265}
System 2 has separation -60.265
system 3 / 100
{'time': 7.4046, 'M1': 5.851, 'M2': 5.873, 'K1': 14.0, 'K2': 14.0, 'separation': -301.45}
System 3 has separation -301.45
system 4 / 100
{'time': 7.4046, 'M1': 5.851, 'M2': 5.873, 'K1': 14.0, 'K2': 14.0, 'separation': -261.9}
System 4 has separation -261.9
system 5 / 100
{'time': 7.4046, 'M1': 5.851, 'M2': 5.873, 'K1': 14.0, 'K2': 14.0, 'separation': -898.13}
System 5 has separation -898.13
system 6 / 100
{'time': 7.4046, 'M1': 5.851, 'M2': 5.873, 'K1': 14.0, 'K2': 14.0, 'separation': -553.0}
System 6 has separation -553.0
system 7 / 100
{'time': 7.4046, 'M1': 5.851, '

How can we help the system become a BHBH merger? We can try turning off SN kicks.

In [6]:
args = dict(
            M_1=60, 
            M_2=40,
            orbital_period=2000, # days    
            BH_prescription='BH_BELCZYNSKI',
            wind_mass_loss='WIND_ALGORITHM_BINARY_C_2020',
            sn_kick_dispersion_II=0,
            sn_kick_dispersion_IBC=0,
            sn_kick_dispersion_GRB_COLLAPSAR=0,
           )
search_for_BHBH(1,**args)

{'M_1': 60, 'M_2': 40, 'orbital_period': 2000, 'BH_prescription': 'BH_BELCZYNSKI', 'wind_mass_loss': 'WIND_ALGORITHM_BINARY_C_2020', 'sn_kick_dispersion_II': 0, 'sn_kick_dispersion_IBC': 0, 'sn_kick_dispersion_GRB_COLLAPSAR': 0}
system 1 / 1
{'time': 7.4046, 'M1': 9.501, 'M2': 9.586, 'K1': 14.0, 'K2': 14.0, 'separation': 9548.9}
System 1 has separation 9548.9
Found bound BHBH system
      TIME      M1       M2   K1  K2           SEP        PER   ECC  R1/ROL1 R2/ROL2  TYPE RANDOM_SEED=32620 RANDOM_COUNT=0
     0.0000   60.000   40.000  1   1        3101.2     5.48 y  0.00   0.009   0.009  "INITIAL "
     0.0000   60.000   40.000  1   1        3101.2     5.48 y  0.00   0.009   0.009  "BEG_SYMB"
     4.3583   42.081   35.930  1   1          3971     8.98 y  0.00   0.023   0.014  "Start tidal lock 1"
     4.3928   41.632   35.894  1   1        3995.8      9.1 y  0.00   0.023   0.014  "End tidal lock 1"
     6.1199   28.792   28.776  1   1        5374.9     16.5 y  0.00   0.014   0.014  "St

You should now have found a BHBH system but usually they have very wide orbits. This is caused by mass loss before, and during, the supernova. 

We can reduce the former by setting the wind mass loss to zero. This can be done unphysically by setting wind_mass_loss=0, or you can reduce the massive-star winds by setting the metallicity to be small, e.g. $10^{-3}$. 

In [7]:
args = dict(
            M_1=60, 
            M_2=40,
            metallicity=0.001,
            orbital_period=2000, # days    
            BH_prescription='BH_BELCZYNSKI',
            wind_mass_loss='WIND_ALGORITHM_BINARY_C_2020',
            sn_kick_dispersion_II=0,
            sn_kick_dispersion_IBC=0,
            sn_kick_dispersion_GRB_COLLAPSAR=0,
           )
search_for_BHBH(1,**args)

{'M_1': 60, 'M_2': 40, 'metallicity': 0.001, 'orbital_period': 2000, 'BH_prescription': 'BH_BELCZYNSKI', 'wind_mass_loss': 'WIND_ALGORITHM_BINARY_C_2020', 'sn_kick_dispersion_II': 0, 'sn_kick_dispersion_IBC': 0, 'sn_kick_dispersion_GRB_COLLAPSAR': 0}
system 1 / 1
{'time': 6.5064, 'M1': 19.536, 'M2': 11.468, 'K1': 14.0, 'K2': 14.0, 'separation': 6493.9}
System 1 has separation 6493.9
Found bound BHBH system
      TIME      M1       M2   K1  K2           SEP        PER   ECC  R1/ROL1 R2/ROL2  TYPE RANDOM_SEED=53854 RANDOM_COUNT=0
     0.0000   60.000   40.000  1   1        3101.2     5.48 y  0.00   0.006   0.006  "INITIAL "
     0.0000   60.000   40.000  1   1        3101.2     5.48 y  0.00   0.006   0.006  "Start Carbon Star 1"
     0.0000   60.000   40.000  1   1        3101.2     5.48 y  0.00   0.006   0.006  "BEG_SYMB"
     3.8674   57.840   39.505  2   1        3185.7     5.78 y  0.00   0.017   0.010  "TYPE_CHNGE"
     3.8704   57.600   39.509  2   1        3192.2      5.8 y  0.00  

Oh dear! While the mass loss is reduced, there is now Roche-lobe overflow (RLOF)! This increases the secondary's mass, but that means it *also* has RLOF. We can try making the system wider to prevent this, but we want a shorter period! Instead, let's shorten the initial period to force common-envelope evolution. This will shrink the system. We will also turn off the mass loss to give us the best change of acquiring the system we want, and turn the SN kicks back on (they have less effect in closer, more grvitationally-bound systems). 

In [8]:
args = dict(
            M_1=60, 
            M_2=40,
            metallicity=0.0001,
            orbital_period=2000, # days    
            BH_prescription='BH_BELCZYNSKI',
            wind_mass_loss='WIND_ALGORITHM_NONE',
            alpha_ce = 0.1,
            lambda_ce = 0.5,
           )
search_for_BHBH(1,**args)

{'M_1': 60, 'M_2': 40, 'metallicity': 0.0001, 'orbital_period': 2000, 'BH_prescription': 'BH_BELCZYNSKI', 'wind_mass_loss': 'WIND_ALGORITHM_NONE', 'alpha_ce': 0.1, 'lambda_ce': 0.5}
system 1 / 1
{'time': 6.0102, 'M1': 24.803, 'M2': 43.622, 'K1': 14.0, 'K2': 14.0, 'separation': -3069.7}
System 1 has separation -3069.7


Note that this system has a far shorter period. Let's run a number of these to see what we find.

In [ ]:
args = dict(
            M_1=60, 
            M_2=40,
            metallicity=0.001,
            orbital_period=2000, # days    
            BH_prescription='BH_BELCZYNSKI',
            wind_mass_loss='WIND_ALGORITHM_NONE',
            alpha_ce=0.1,
           )

found = False
while found == False:
    d = search_for_BHBH(100,**args)
    if d != None and d['separation'] < 10.0:
        found = True
    


{'M_1': 60, 'M_2': 40, 'metallicity': 0.001, 'orbital_period': 2000, 'BH_prescription': 'BH_BELCZYNSKI', 'wind_mass_loss': 'WIND_ALGORITHM_NONE', 'alpha_ce': 0.1}
system 1 / 100
{'time': 6.1851, 'M1': 26.215, 'M2': 48.508, 'K1': 14.0, 'K2': 14.0, 'separation': -266.67}
System 1 has separation -266.67
system 2 / 100
{'time': 6.2266, 'M1': 26.334, 'M2': 16.879, 'K1': 14.0, 'K2': 14.0, 'separation': 41.945}
System 2 has separation 41.945
Found bound BHBH system
      TIME      M1       M2   K1  K2           SEP        PER   ECC  R1/ROL1 R2/ROL2  TYPE RANDOM_SEED=60876 RANDOM_COUNT=0
     0.0000   60.000   40.000  1   1        3101.2     5.48 y  0.00   0.006   0.006  "INITIAL "
     0.0000   60.000   40.000  1   1        3101.2     5.48 y  0.00   0.006   0.006  "Start Carbon Star 1"
     3.7617   60.000   40.000  2   1        3101.2     5.48 y  0.00   0.018   0.010  "TYPE_CHNGE"
     3.7647   60.000   40.000  2   1        3101.2     5.48 y  0.00   0.572   0.010  "Start tidal lock 1"
     3